<br><br>
<h1 style="font-family:'Verdana',sans-serif; color:#1D7874; font-size:30px;">Transmission system operation</h1>

<br>
<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">Table of Contents</h3>
<br>
<ol style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    <li ><a href='#introduction'>Introduction</a></li>
    <li ><a href='#motivation'>Motivation</a></li>
    <li><a href='#load_env'>Load an environment with grid2op</a></li>
    <li><a href='#grid_info'>Grid information and electrical losses</a></li>
    <li><a href='#grid'>The 5 substation grid</a></li>
    <li><a href='#line_cut'>A line disconnection and its effect</a></li>
    <li><a href='#config'>Inside a substation</a></li>
    <li><a href='#remedial'>A remedial solution</a></li>
    <li><a href='#conclusion'>Conclusion</a></li>
</ol>

<a id='introduction'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">1. Introduction</h3>
<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    This notebook is an introduction to power system operations and the grid2op pacakge. The operation of electrical power grids have been studied for many years around the world and involves many activities. Power grids, especially transmission grid, aims to transporting electricity over long distances from power plants to consumers. To be efficient and minimize energy losses, power grids often operate under high voltages (above 20kV). One of the main goals for power grid operators is to ensure a reliable and secure continuity of delivery of electricity to consumers under some additional quality criterion that can vary from one country to another.      
<br><br>
    For simplicity, a four substations grid is presented here with producers and consumers meshed through a grid. However, transmission grids are more complex and involve many long lines that connect different cities or states. A grid often connects an entire country linking hundreds of power plants and distribution networks but our current example should illustrate clearly enough how congestion could arise on the power grid and which operation could help manage it. Congestion management is actually the most critical and time-consuming task for a power grid operator.
<br><br>
    <img src="utils/img/Example-Grid.jpg", width=650, ALIGN="middle", border=20>
<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:center; font-size:11px;">
(courtesy by Marvin Lerousseau -- if images does not display correctly, make sure to start the jupyter notebook server from the root directory of the starting kit.)
</p>
</p>
<br><br> 
For more information on the grid2op platforme, some explanatory notebooks are available withing the package of this plateform located at <a href="https://github.com/rte-france/Grid2Op">https://github.com/rte-france/Grid2Op</a>. If these notebooks still do not answer your question, a technical documentation on most of the platform can is available online at <a href="https://grid2op.readthedocs.io/">https://grid2op.readthedocs.io/</a>. 

<a id='motivation'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">2. Motivation</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    A power line has some physical capacity, aka thermal limit as illustrated in the figures below.
    <img src="utils/img/Powerline_ok.png", width=650, ALIGN="middle", border=20> <b>Situation ok</b> Not a lot of flows are flowing on this powerline. It is far from the tree bellow it, thus presenting very little risk.
    <img src="utils/img/Powerline_tense.png", width=650, ALIGN="middle", border=20> <b>Situation at risk</b> More current flows on the powerline. Due to <a href="https://en.wikipedia.org/wiki/Joule_heating">Joule heating</a> it gets hotter and gets closer to the tree bellow it. Typically, powergrids operators want to be alerted when such a situation is becoming critical.
    <img src="utils/img/Powerline_ko.png", width=650, ALIGN="middle", border=20> <b>Too late to act</b> Even More current flows on the powerline. Due to Joule heating it gets even hotter and ends up in contact with the tree. At this point nothing can be made. The tree can catch fire (due to heat), the powerline can break etc. This situation should be avoided.
    <br><br>
    To prevent this potentially dramatic effect, power lines are often equiped with "sensors" that detects when the flows is above a certain threshold (called "<b>thermal limit</b>"), typically in the second figure above. And if the flows is above this thermal limit for a given amount of time, then the powerline is <b>automatically</b> disconnected form the powergrid without any human intervention. To prevent the disconnection of more and more powerlines (phenomenon called "cascading failure") operators often prefers to act <i>before</i> the powerline is disconnected and try to re route the flows in other powerlines.
<br><br>
    To be as efficient as possible operators monitor the grid in real time. They know the power flowing through all the powerlines of the grid and it allows them to anticipated problems by relying on their expertise and making extensive simulations requiring "powerflow solver" that can compute how much power flow on each powerlines given the productions and consumptions location as well as the topology of the powergrid.
<br><br>
    As a first intuition, power flows increase when electrical consumption increases. More specifically, the flows in lines are affected by the dynamics of power consumption and the availability of power plants or productions. It often varies along the course of a day, as consumer behaviors and usages change depending on the hour of the day: there are more activities in the middle of the day, while lighting is used mostly overnight and people finally get to sleep, leaving mostly electrical heating systems as well as some few industries in operations.   
<br><br>  
    The congestion could be caused by day to day demand, but can also be due to some external factors such as topology grid changes by operator's actions, lines in maintenance or transient faults that can lead to cascading failures or put the system in instable conditions.
</p>

<a id='load_env'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">3. Loading the environment</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    Grid2Op is an open-source platform that relies on powerflow solvers (typically pandapower) to compute the power flows in a grid. The main focus of this package is to be able to interact with the powergrid allowing to adopt a  <i>Reinforcement Learning</i> approach.
<br><br>
    Right now, we are going to load all libraries and grid2op environment. The environment contains all essential information about the power grid such as the substations ids where the loads, generators and transmission lines are connected, the power flows and so on.
</p>

In [1]:
import warnings
import os
import numpy as np
import pandas as pd
%matplotlib inline
import matplotlib.pyplot as plt
import grid2op
from grid2op.MakeEnv import make
from grid2op.PlotPlotly import PlotObs

pygame 1.9.6
Hello from the pygame community. https://www.pygame.org/contribute.html


/home/donnotben/.local/lib/python3.6/site-packages/pandapower/io_utils.py:8: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  from pandas.util.testing import assert_series_equal, assert_frame_equal


In [2]:
# Initialize the environment
environment = make("case5_example")

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    A powergrid has been loaded, it consists a grid with 5 substations, 8 powerlines, 3 loads and 2 generators. It is displayed in the next cell.
    <br><br>
    Though perfectly adapted for smaller grid, this kind of representation is not advised when dealing with powergrid with more than 10-15 substations.
</p>

In [3]:
graph_layout =  [(0,0), (0,400), (200,400), (400, 400), (400, 0)]
plot_helper = PlotObs(substation_layout=graph_layout, observation_space=environment.observation_space)

fig = plot_helper.get_plot_observation(environment.get_obs())
fig.show()

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
Another representation of the powergrid, where generators and loads location as well as label for each powerline and generators load is:
    <img src="utils/img/grid.png", width=650, ALIGN="middle", border=20>
</p>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">4. Grid Information and electrical losses</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
Despide the grid is very small and simple, all information is accessible directly using the grid2op environment. Let's get some information about the most important objects over a power grid: power lines, electrical bus, loads (aka consumptions) and generators (aka productions). 
<br><br>
    The state of those objects are very important in the reinforcement learning challenge as they will be used in observations. It means that given you observe the switch status, power flows, etc the agent should be able to take the correct action to keep flows in normal condition as possible. The following lines of code retrieve the nodes or substations ids and the numbers of elements connected to each busbar. 
</p>

In [4]:
# Load ids
print("\nInjection information:")
load_to_subid = environment.load_to_subid
print ('\t- There are {} loads connected to substations with id: {}'.format(len(load_to_subid), load_to_subid))

# Generators irds
gen_to_subid = environment.gen_to_subid
print ('\t -There are {} generators, connected to substations with id: {}'.format(len(gen_to_subid), gen_to_subid))

# Line id sender
print("\nPowerline information:")
line_or_to_subid = environment.line_or_to_subid
line_ex_to_subid = environment.line_ex_to_subid
print ('There are {} transmissions lines on this grid. They connect:'.format(len(line_or_to_subid)))
for ori, ext in zip(line_or_to_subid, line_ex_to_subid):
    print("\t- Substation origin id {} to substation extremity id {}".format(ori, ext))

# Num of elements per SE
print("\nSubstations information:")
for i, nb_el in enumerate(environment.sub_info):
    print("\t-On susbtation {} there are {} elements.".format(i, nb_el))



Injection information:
	- There are 3 loads connected to substations with id: [0 3 4]
	 -There are 2 generators, connected to substations with id: [0 1]

Powerline information:
There are 8 transmissions lines on this grid. They connect:
	- Substation origin id 0 to substation extremity id 1
	- Substation origin id 0 to substation extremity id 2
	- Substation origin id 0 to substation extremity id 3
	- Substation origin id 0 to substation extremity id 4
	- Substation origin id 1 to substation extremity id 2
	- Substation origin id 2 to substation extremity id 3
	- Substation origin id 2 to substation extremity id 3
	- Substation origin id 3 to substation extremity id 4

Substations information:
	-On susbtation 0 there are 6 elements.
	-On susbtation 1 there are 3 elements.
	-On susbtation 2 there are 4 elements.
	-On susbtation 3 there are 5 elements.
	-On susbtation 4 there are 3 elements.


<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
The Grid2Op package offers to perform actions on the powergrid. It also allows the powergrid to be modified by the environment (load can increase because lots of people are getting home and start to heat their appartment for example).
    <br><br>
    In the L2RPN competition, you are asked to adapted the powergrid to face these changes. These changes are "automatically" performed on the powergrid when calling "environment.step(agent_action)" function. This function expects the agent to give the action it has performed at this timestep. This mechanism is explained in the cell bellow, where we suppose the agent take the "do nothing" action (eg. it does not change anything to the state of the powergrid.)
</p>

In [5]:
action_space = environment.action_space
observation_space = environment.observation_space

# Create do_nothing action.
agent_action = action_space({}) # this is the do nothing action

In [6]:
# Run one step in the environment
obs, *_ = environment.step(agent_action)
print (type(obs))

<class 'grid2op.Observation.CompleteObservation'>


<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
As you see the observation is a nspecial class. Sometimes is better to transform it as a vector in the following way:
</p>

In [7]:
obs_as_vect = obs.to_vect()
print(obs_as_vect)

[ 2.01900000e+03  1.00000000e+00  1.00000000e+00  0.00000000e+00
  1.00000000e+01  1.00000000e+00  1.70000000e+00  2.58836408e+01
  1.53004910e+02 -1.54597290e+02  1.02000000e+02  1.02000000e+02
  8.70000000e+00  7.80000000e+00  8.10000000e+00  6.10000000e+00
  5.50000000e+00  5.70000000e+00  1.02000000e+02  1.01891698e+02
  1.01838128e+02 -9.29031639e+00 -2.22259328e+00  2.63984592e-01
  4.24892508e+00  1.50771758e+01  5.88759181e+00  5.88759181e+00
  3.98139683e+00  7.64489279e+01  3.44619596e+01  2.02373940e+01
  1.57566285e+01 -7.55988240e+01 -1.84191194e+01 -1.84191194e+01
 -1.55192609e+01  1.02000000e+02  1.02000000e+02  1.02000000e+02
  1.02000000e+02  1.02000000e+02  1.01936713e+02  1.01936713e+02
  1.01891698e+02  4.35907114e+02  1.95470183e+02  1.14559401e+02
  9.23729745e+01  4.36338888e+02  1.09522302e+02  1.09522302e+02
  9.07846962e+01  1.08064650e+01  2.58135340e+00 -9.24987371e-02
 -4.17204555e+00 -1.43565370e+01 -5.84444905e+00 -5.84444905e+00
 -3.92795445e+00 -7.89984

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
Please refer to the official getting_started notebooks <a href="https://github.com/rte-france/Grid2Op/tree/master/getting_started">here</a> for more informations.
    <br>
    They can be launched interactively with the help of "mybinder" at the following address:
    https://mybinder.org/v2/gh/rte-france/Grid2Op/master
    <br>
    For more information on mybinder, visit <a href="https://mybinder.org/">https://mybinder.org/</a>
</p>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
The next function allows us to perform a few iterations using the step method in the environment given an action as an input and returns the observation variables as the power flow results, switches states, etc.
</p>

In [8]:
import copy

def sim(action, 
        t_action=0):
    
    # Restart all the game from the scratch.
    env = None
    env = make("case5_example")    
    obs_as_class = None
    obs_as_vect = None
    # Iterating process..
    for i in range(t_action+1):
        obs_as_class, reward, done, info = env.step(action)
        obs_as_vect = obs_as_class.to_vect()
        if done:
            raise RuntimeError("Impossible to complete the scenario. GAME OVER.")
    return env, obs_as_class, obs_as_vect

In [9]:
env, obs, osb_as_vect = sim(agent_action, t_action=3)
fig = plot_helper.get_plot_observation(obs)
fig.show()

<a id='grid'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">5. A simple grid</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
The five substation grid is presented as follows. All power plants, consumptions and lines are on service and the load flows are indicating in each substation.
</p>

<div class="alert alert-warning">
    Note: How to interprate the flows?... A powergrid can be modeled as an oriented graph. Powerline have then an "origin" and an "extremity" representing the direction of the powerlines (from "origin" to "extremity"). This means that is there is a positive flow, the actual powerflow goes from origin to extremity, if the powerflow is negative, this means it goes from extremity to origin.
    <br>
    Due to losses, one will notice that the flows getting out of the powerline at the origin bus (node) is not equal to the powerflow entering at the extremity bus. This is because some power is "lost" during the transportation. Typical losses are about 2% of the total consumption of the powergrid.
</div>

In [10]:
# Run the game.
t_action = 5

# Run the environment.
env, obs, obs_as_vect = sim(agent_action, t_action=t_action)

fig = plot_helper.get_plot_observation(obs)
fig.show()

<h4 style="font-family:'Verdana',sans-serif; color:#1D7874;">How to interpret the results?</h4>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
The values of the power flows are attached reprenseted by the color of the powegrid the more red, the more flow there is. In this case the situation is not really good. With most of the powerline being loaded at 90% the situation is quite tense;
</p>

<a id='line_cut'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">6. Line disconnection</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    Transmission lines link different states or regions between productions and consumptions. They have long distance and are subjected to suddenly disconnections due to thunderstorms. It is natural to have one or more lines out-of-service along the day because of thunder hits a line. This number tends to increase during winter. 
<br><br>
    A disconnected line changes the configuration on the grid and causes a power flow's redistribution in the grid. Sometimes these undesired events lead to some overloads in other lines. You have not guess the reason why yet? The answer is very intuitive. When a line get disconnected, the same amount of energy is still demanded by customers, but now you have one less path in the grid to transport the energy, and the others will hence be loaded with more power.
<br><br>
    Substations are equipped with switches to disconnect a line when a fault or congestion is detected (as explained in the first section of this notebook). Normally the criteria to disconnect a line under a congestion is to measure the flow and the time a line remains congested above a given threshold the switch automatically open a line.
<br><br>
    This behavior occurs many times in electrical systems and the expertise and vast knowledge of operators help to alleviate the stress in order to guarantee energy to customers. A similar action could be replicated using grid2op. We simulate a disconnection in our small grid to see the resultant state of the grid.
    <br><br>
    In the few next cells we will explain how to disconnect powerlines. First we create the action that will tell the grid to disconnect a powerline. Then we apply it on the grid, and then we look at the result.
</p>

<div class="alert alert-warning">
    Note: The user can modify and play with other lines.
</div>

In [11]:
# Specify the disconnection of line with id 2 (it's python, so id starts at 0)
id_line = 2
# Initialize action class
action = action_space({"set_line_status": [(id_line, -1)]})
print(action)

This action will:
	 - NOT change anything to the injections
	 - NOT perform any redispatching action
	 - force disconnection of 1 powerlines ([2])
	 - NOT switch any line status
	 - NOT switch anything in the topology
	 - NOT force any particular bus configuration


<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
Make an environment and look at the powergrid:
</p>

In [12]:
# Run simulation
environment = make("case5_example")
init_obs = environment.get_obs()
fig = plot_helper.get_plot_observation(init_obs)
fig.show()

In [13]:
obs_as_class, reward, done, info = environment.step(action)
print("Grid State after disconnection of powerline with id 2:")
fig = plot_helper.get_plot_observation(obs_as_class)
fig.show()

Grid State after disconnection of powerline with id 2:


<h4 style="font-family:'Verdana',sans-serif; color:#1D7874;">Analyzing results...</h4>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
In the previous results, we simulated a line disconnection caused by a lightning in the path 1-2. You immediately may notice some lines have changed the color. Overload events have been detected over the lines 1-4 and 1-3. The resulting power flow, after the redistribution, causes a  flow increments over their thermal limits. In such condition, electrical operators have a few minutes to execute remedial actions to alleviate the system.
    <br>
    We can more qualitatively measure the difference of some flows.
</p>

In [14]:
print("The difference in the current flows at the origin of powerlines is:\n{}".format(obs_as_class.a_or - init_obs.a_or))

The difference in the current flows at the origin of powerlines is:
[ -10.06438784   27.36021026 -116.50533305   28.34172692  -79.90703863
  -49.76020435  -49.76020435   28.31287501]


<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    In this case, disconnecting powerline with id 2 will (for example) reduce the flows of the the powerline with id 0 of 10 amperes, but will increase the flows on powerline with id 1 of 27 amperes
    <br><br>
    We can also have a look at the ratio "current flows / thermal limit" on each powerline, and compare them:
    </p>

In [15]:
print("The difference in the loading of powerlines is:\n{}".format(obs_as_class.rho - init_obs.rho))

The difference in the loading of powerlines is:
[-0.01677398  0.12436459 -0.72815833  0.17713579 -0.1331784  -0.16586735
 -0.16586735  0.17695547]


<a id='config'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">7. Inside a Substation</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    A power grid is composed of power lines connected through substations. Within a substation, there can be several arrangements between branches (lines, generators and loads) that allow them to meet. There exist many predefined configurations and each of them are better than others in terms of reliability.
<br><br>
    In grid2op, substations have "double busbar layout", which means that you can make no more than two electrical nodes per substations. The double busbar configuration consists of two bars on which you can connect together generators, loads and lines. For each of those elements, you have to choose the busbar it is connected to at a given time. The following figure is a representation of such configuration.
<br><br>
    <img src="utils/img/bus_bar.png", width=800, ALIGN="middle">
<br><br>
     <b> On the left</b> you can the modeling of the substation 1 of the powergrid. It is composed of 2 busbar, named "bus 1" (blue) and "bus 2" (orange). Each object (in this case: consumption c1, production p1, and origin of powerline l1, origin of powerline l2, origin of powerline l3 and origin of powerline l4 and origin of powerline l5) can be connected either to bus 1 or to bus 2. We showed the example where l1, l2 and c1 are connected to bus 1 and p2, l2 and l4 are connected to bus 1. There is no connection between these bus 1 and bus 2. <b> On the right </b> is the representation as a graph of the relevant powergrid.
    <br><br>
    Note that to simplify the action the Agents don't act directly on the switches (which would add some constraints on the problem, for example, an element can be connected on only one busbar: one switch open at most). In grid2op we choose to have people specifying on which bus the object is connected. The switch states are handled directly by the platform.
</p>

<a id='remedial'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">8. A Remedial Action</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    When an overload is detected, operators have to execute a remedial action to alleviate the stress in the system. Normally the experience gained by years by people who work in electrical control rooms is a crucial factor to determine the best one. 
<br><br>
    Transmission networks are a bit complex with many paths where the power can flow (mesh grids). This also gives many alternatives to solve the congestions. In many countries changing the production is a valid solution. For instance, you can decrease the production of the generators which are connected to the overloaded line and increase others that are near the consumptions and it will reduce the overall flows on the powergrid.
<br><br>
    However, the previous one is costly, especially in countries where producers are market actors. An always cheap one is to play with the main grid configuration, thus one does not have to change the productions. These are the kind of actions Rte wants to use to build a new smart controllers for the power grid through the challenge. 
<br><br>
    To illustrate the issue, let's take a step back to the previous grid state. Let's imagine something disconnected the powerline with id 2 (connecting subsation 0 with substation 3) on the powergrid (the powergrid is showed in the figure <b>"Grid State after disconnection of powerline with id 2:"</b> above). As we can see, this powergrid is not safe at all. The current flow on powerline with id 1 (connecting substation 0 and substation 2) is at 100% of its thermal limit. Something need to be done !
<br><br>
    In this section we will see if performing a node splitting of substation with id 2 will solve the problem. The proposed action to performed is equivalent to change from the grid represented on the left, to the grid represented on the right in the figure below:
    <img src="utils/img/grid_2nodes.png", width=800, ALIGN="middle">
</p>

In [16]:
# SE id we want to modify.
sub_id = 2

In [17]:
id_l2_ingrid, *_ = environment.get_lines_id(from_=0, to_=sub_id)
# we know l2 is connected to its "extremity" end at substation 2, so we look at its position in this substation 
# for its extremity part
id_in_sub2_l2 = environment.line_ex_to_sub_pos[id_l2_ingrid]

id_l5_ingrid, *_ = environment.get_lines_id(from_=1, to_=sub_id)
id_in_sub2_l5 = environment.line_ex_to_sub_pos[id_l5_ingrid]

id_l6l7_ingrid = environment.get_lines_id(from_=sub_id, to_=3)
# we know l6 and l7 are connected to their "origin" end at substation 2, so we look at its position in this substation 
# for its origin part
id_in_sub2_l6 = environment.line_or_to_sub_pos[id_l6l7_ingrid[0]]
id_in_sub2_l7 = environment.line_or_to_sub_pos[id_l6l7_ingrid[1]]

In [18]:
# now we tell we want l5 connected to l6 and l2 to l7.
# we can achieve that, for example, by changing the bus of l2 and l7, but not the one of l5 and l6.
# this way, l5 and l6 will stay connected to bus 1 in substation with id 2 and l2 and l7 will be connected to bus 2.

modified_bus = np.full(shape=4, dtype=bool, fill_value=False)
# 4 because there are 4 elements in substation with id 2
modified_bus[id_in_sub2_l2] = True
modified_bus[id_in_sub2_l7] = True
applied_action = environment.action_space({"change_bus": {"substations_id": [(sub_id, modified_bus)]}})
print(applied_action)

This action will:
	 - NOT change anything to the injections
	 - NOT perform any redispatching action
	 - NOT force any line status
	 - NOT switch any line status
	 - Change the bus of the following element:
	 	 - switch bus of line (extremity) 1 [on substation 2]
	 	 - switch bus of line (origin) 6 [on substation 2]
	 - NOT force any particular bus configuration


In [19]:
# Run the environment.
after_obs, reward, done, info = environment.step(applied_action)

# Plot the grid.
if not done:
    print("Grid State after the proposed topological action:")
    fig = plot_helper.get_plot_observation(after_obs)
    fig.show()
else:
    print("Unfortunately the solution caused a lot of trouble, no powerflow can be computed by the solver."
          "This is a GAME OVER")

Grid State after the proposed topological action:


<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    The proposed solution solved the problem for powerline with id 1 without creating new problem. The agent sucessfully overcome this difficulty.    
</p>

<a id='conclusion'></a>

<h3 style="font-family:'Verdana',sans-serif; color:#1D7874;">9. Conclusion</h3>

<p style="font-family:'Verdana','sans-serif'; color:#393D3F; text-align:justify; font-size:14px;">
    In this notebook, we reviewed very quickly the main operation principles in transmission networks with a small grid. The continuity of the electric power service is crucial for nowadays economy and should be robust enough to any hazards or atypical sistuations in its operations. A undesired line disconnection without an effective action that could solve the problem might bring blackouts and economic losses. 
<br><br>
    As we mentioned earlier, transmission operation involves many tasks but all of them are met to have one single objective: supply reliable and secure electricity. Operators work every day to minimize the impact of external factors that put the electrical system at risk but eventually when the grid is large and meshed, the daily operation is more complicated.
<br><br>
    The Grid2Op platform was designed to interact together with the reinforcement learning approach. It allows executing actions in the transmission grid to manage lines with congestion without any cost involved. We covered all actions such as line disconnection and node splitting in the respective section. A user could play and execute more complicated ones through combinations.  
<br><br>
    The end state during the challenge is to train an agent able to learn a policy that could overcome obstacles, aka congestions, while optimizing the line usage rates to reflect a real operation in transmission grids.
</p>